In [1]:
#Import Libraries
import numpy as np
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point, Polygon
import json
import requests
import math
import os
import time
import datetime
import itertools

In [2]:
# Import folders
data_folder = os.path.abspath('data')
# Set Output Folder
output_folder = os.path.abspath("output")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)
if not os.path.exists(os.path.join(output_folder, 'joined')):
    os.makedirs(os.path.join(output_folder, 'joined'))
    
if not os.path.exists(os.path.join(output_folder, 'joined', 'Physical Progress Reports')):
    os.makedirs(os.path.join(output_folder, 'joined', 'Physical Progress Reports'))
    
    
    

In [3]:
# Helping Functions
def remove_consecutive_duplicates(x):
    return ''.join(i for i, _ in itertools.groupby(x))

In [4]:
# Read Constituency Data
ac_gdf = None
ac_filepath = os.path.join(data_folder, "AC", "India_AC.shp")
ac_gdf = gpd.read_file(ac_filepath)
ac_gdf

ac_geocode_df = ac_gdf[ac_gdf.columns[:-3]]

# Read Constituency Data
ac_file = os.path.join(data_folder, "General_Later_Ashoka_alldata.csv")
acdf = pd.read_csv(ac_file)
acdf['state_name'] = acdf['state_name'].str.replace("_", " ")
#acdf = acdf[['state_name', 'constituency_no', 'constituency_name', 'year', 'month']]
acdf = acdf.drop_duplicates(subset=None, keep="first", inplace=False).reset_index(drop=True)
acdf.loc[acdf['newstate_code'] == 36, 'newstate_code'] = 28 #Telangana  Fix
acdf = acdf[['state_name', 'state_code', 'constituency_no', 'year', 'month']]
acdf['day'] = 1
acdf['dyear'] = 0
acdf.loc[(acdf['month'] > 9) | (acdf['year'] == 2008), 'dyear'] = 1
acdf['dyear'] = acdf['year'] + acdf['dyear']
acdf['datetime'] = pd.to_datetime(acdf[['year', 'month', 'day']])
acdf = acdf.drop_duplicates().reset_index(drop=True)
acdf = pd.merge(acdf, ac_gdf,  how='inner', left_on=['state_code', 'constituency_no'], right_on = ['ST_CODE','AC_NO'])#[['ST_CODE', 'ST_NAME','DT_CODE', 'DIST_NAME', 'AC_NO', 'AC_NAME', 'PC_NO', 'PC_NAME']]
acdf = acdf[acdf.columns[:-5]]
acdf

state_name  state_code  constituency_no  year  month  day  dyear  \
0     Jammu & Kashmir           1                1  2008     12    1   2009   
1     Jammu & Kashmir           1                1  2014     12    1   2015   
2     Jammu & Kashmir           1                2  2008     12    1   2009   
3     Jammu & Kashmir           1                2  2014     12    1   2015   
4     Jammu & Kashmir           1                3  2008     12    1   2009   
5     Jammu & Kashmir           1                3  2014     12    1   2015   
6     Jammu & Kashmir           1                4  2008     12    1   2009   
7     Jammu & Kashmir           1                4  2014     12    1   2015   
8     Jammu & Kashmir           1                5  2008     12    1   2009   
9     Jammu & Kashmir           1                5  2014     12    1   2015   
10    Jammu & Kashmir           1                6  2008     12    1   2009   
11    Jammu & Kashmir           1                6  2014     12    1   2015   
12    Jammu & Kashmir           1                7  2008     12    1   2009   
13    Jammu & Kashmir           1                7  2014     12    1   2015   
14    Jammu & Kashmir           1                8  2008     12    1   2009   
15    Jammu & Kashmir           1                8  2014     12    1   2015   
16    Jammu & Kashmir           1                9  2008     12    1   2009   
17    Jammu & Kashmir           1                9  2014     12    1   2015   
18    Jammu & Kashmir           1               10  2008     12    1   2009   
19    Jammu & Kashmir           1               10  2014     12    1   2015   
20    Jammu & Kashmir           1               11  2008     12    1   2009   
21    Jammu & Kashmir           1               11  2014     12    1   2015   
22    Jammu & Kashmir           1               12  2008     12    1   2009   
23    Jammu & Kashmir           1               12  2014     12    1   2015   
24    Jammu & Kashmir           1               13  2008     12    1   2009   
25    Jammu & Kashmir           1               13  2014     12    1   2015   
26    Jammu & Kashmir           1               14  2008     12    1   2009   
27    Jammu & Kashmir           1               14  2014     12    1   2015   
28    Jammu & Kashmir           1               15  2008     12    1   2009   
29    Jammu & Kashmir           1               15  2014     12    1   2015   
...               ...         ...              ...   ...    ...  ...    ...   
8328       Puducherry          34               16  2011      5    1   2011   
8329       Puducherry          34               16  2016      5    1   2016   
8330       Puducherry          34               17  2011      5    1   2011   
8331       Puducherry          34               17  2016      5    1   2016   
8332       Puducherry          34               18  2011      5    1   2011   
8333       Puducherry          34               18  2016      5    1   2016   
8334       Puducherry          34               19  2011      5    1   2011   
8335       Puducherry          34               19  2016      5    1   2016   
8336       Puducherry          34               20  2011      5    1   2011   
8337       Puducherry          34               20  2016      5    1   2016   
8338       Puducherry          34               21  2011      5    1   2011   
8339       Puducherry          34               21  2016      5    1   2016   
8340       Puducherry          34               22  2011      5    1   2011   
8341       Puducherry          34               22  2016      5    1   2016   
8342       Puducherry          34               23  2011      5    1   2011   
8343       Puducherry          34               23  2016      5    1   2016   
8344       Puducherry          34               24  2011      5    1   2011   
8345       Puducherry          34               24  2016      5    1   2016   
8346       Puducherry          34               25  2011     

In [5]:
# Read geocoded Scrapped Data
geocoded_file = os.path.join(data_folder, 'geocoded.csv')
geocoded_df = pd.read_csv(geocoded_file)
geocoded_df['district_y'] = geocoded_df['district'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
geocoded_df['panchayat_y'] = geocoded_df['panchayat'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
geocoded_df = pd.merge(geocoded_df, ac_geocode_df,  how='left', left_on=['ac_code', 'state_code'], right_on = ['AC_NO', 'ST_CODE'])
#geocoded_df.drop_duplicates()
geocoded_df = geocoded_df[geocoded_df.columns[5:]].drop_duplicates()
geocoded_df

district_y       panchayat_y  OBJECTID  ST_CODE  ST_NAME  DT_CODE  \
0           ARARIA       ARARIABASTI       9.0     10.0    BIHAR      7.0   
1           ARARIA           BANGAMA       9.0     10.0    BIHAR      7.0   
2           ARARIA          BANSBARI       9.0     10.0    BIHAR      7.0   
3           ARARIA         BASANTPUR       9.0     10.0    BIHAR      7.0   
4           ARARIA         BATURBARI       9.0     10.0    BIHAR      7.0   
5           ARARIA             BELWA       9.0     10.0    BIHAR      7.0   
6           ARARIA             BOCHI       9.0     10.0    BIHAR      7.0   
7           ARARIA            CHATAR       9.0     10.0    BIHAR      7.0   
8           ARARIA            DIYARI       9.0     10.0    BIHAR      7.0   
9           ARARIA           GAIYARI       9.0     10.0    BIHAR      7.0   
10          ARARIA          HAYATPUR       9.0     10.0    BIHAR      7.0   
11          ARARIA             JAMUA       9.0     10.0    BIHAR      7.0   
12          ARARIA            JHAMTA       9.0     10.0    BIHAR      7.0   
13          ARARIA         KAMALDAHA       9.0     10.0    BIHAR      7.0   
14          ARARIA         KAMALDAHA       9.0     10.0    BIHAR      7.0   
15          ARARIA   KISMATKHAWASPUR       9.0     10.0    BIHAR      7.0   
16          ARARIA          PAIKTOLA       9.0     10.0    BIHAR      7.0   
17          ARARIA   RAMPURKODARKATI       9.0     10.0    BIHAR      7.0   
18          ARARIA          SAHASMAL       9.0     10.0    BIHAR      7.0   
19          ARARIA         SHARANPUR       9.0     10.0    BIHAR      7.0   
20          ARARIA          BAGNAGAR       9.0     10.0    BIHAR      7.0   
21          ARARIA    BARAISTAMBARAR       9.0     10.0    BIHAR      7.0   
22          ARARIA        BHAGWANPUR       9.0     10.0    BIHAR      7.0   
23          ARARIA      BHUNAMAJGAMA       9.0     10.0    BIHAR      7.0   
24          ARARIA            CHAKAI       9.0     10.0    BIHAR      7.0   
25          ARARIA            CHIRAH       9.0     10.0    BIHAR      7.0   
26          ARARIA              DUBA       9.0     10.0    BIHAR      7.0   
27          ARARIA             GIRDA       9.0     10.0    BIHAR      7.0   
28          ARARIA            HARDAR       9.0     10.0    BIHAR      7.0   
29          ARARIA             KAKAN       9.0     10.0    BIHAR      7.0   
...            ...               ...       ...      ...      ...      ...   
280963    SENAPATI        MOLKONBUNG       1.0     14.0  MANIPUR      5.0   
280964    SENAPATI    POIROUTANGKHUL       1.0     14.0  MANIPUR      5.0   
280965   GURDASPUR              DHIR       1.0      3.0   PUNJAB      1.0   
280966   GURDASPUR          LONGOWAL       1.0      3.0   PUNJAB      1.0   
280967   PATHANKOT        HABATPINDI       1.0      3.0   PUNJAB      1.0   
280968   GURDASPUR    KOTLABAJASINGH       5.0      3.0   PUNJAB      1.0   
280969   GURDASPUR            KHUNDI       5.0      3.0   PUNJAB      1.0   
280970  HOSHIARPUR             CHEMA       5.0      3.0   PUNJAB      5.0   
280971  HOSHIARPUR             DAGAN       5.0      3.0   PUNJAB      5.0   
280972  HOSHIARPUR            KOLPUR       5.0      3.0   PUNJAB      5.0   
280973  HOSHIARPUR              ULAH       5.0      3.0   PUNJAB      5.0   
280974  HOSHIARPUR            BAROTI       5.0      3.0   PUNJAB      5.0   
280975  HOSHIARPUR   BASIGULAMHUSAIN       5.0      3.0   PUNJAB      5.0   
280976  HOSHIARPUR          SAINCHAN       5.0      3.0   PUNJAB      5.0   
280977  HOSHIARPUR            SARAIN       5.0      3.0   PUNJAB      5.0   
280978  HOSHIARPUR  BAHADURPURBAHIAN       5.0      3.0   PUNJAB      5.0   
280979  HOSHIARPUR         CHAKSADHU       5.0      3.0   PUNJAB      5.0   
280980  HOSHIARPUR            CHOHAL       5.0      3.0   PUNJAB      5.0   
280981  HOSHIARPUR              DADA       5.0      3.0   PUNJAB      5.0   
280982  HOSHIARPUR           HARMOYA       5.0      3.0   PUNJAB      5.0   
2809

In [21]:
# Read physical progress Data
physical_progress_folder = os.path.join(data_folder, "Physical Progress Reports", "output")
physical_progress_files = os.listdir(physical_progress_folder)
physical_progress_files = [x for x in physical_progress_files if x.split('.')[-1] == 'csv'][:-1]
df_list = []
for file in physical_progress_files:
    print(file)
    physical_df = pd.read_csv(os.path.join(physical_progress_folder, file))
    physical_df = physical_df[physical_df['Panchayat Name'].notnull()]
    physical_df['Panchayat Name'] = physical_df['Panchayat Name'].str.upper()
    physical_df['Panchayat Name'] = physical_df['Panchayat Name'].str.replace('PANCHAYAT', '').str.replace('GP', '')
    physical_df['District Name'] = physical_df['District Name'].str.upper()
    physical_df['State Name'] = physical_df['State Name'].str.upper()
    physical_df['dyear'] = physical_df['Financial Year'].str.split('-').str[0].fillna(0).astype(int)
    physical_df['district_y'] = physical_df['District Name'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
    physical_df['panchayat_y'] = physical_df['Panchayat Name'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
    physical_df = pd.merge(physical_df, geocoded_df, how='left', on=['panchayat_y', 'district_y'])
    #physical_df = physical_df[physical_df['ac_code'].notnull()]
    #Output to CSV
    physical_df.to_csv(os.path.join(output_folder, 'joined', "Physical Progress Reports", file), encoding='utf-8', index=False)
    

2010-2011_Scrapped_Data.csv
2011-2012_Scrapped_Data.csv
2012-2013_Scrapped_Data.csv
2013-2014_Scrapped_Data.csv
2014-2015_Scrapped_Data.csv
2015-2016_Scrapped_Data.csv
2016-2017_Scrapped_Data.csv
2017-2019_Scrapped_Data.csv


In [6]:
# Read All Central Scheme Financial progress Data
centr_folder = os.path.join(data_folder, "Financial Progress Reports", "All Central Scheme-done", "output")
centr_files = os.listdir(centr_folder)
centr_files = [os.path.join(centr_folder, x)  for x in centr_files if x.split('.')[-1] == 'csv'][:-1]
df_list = []
for file in centr_files:
    df = pd.read_csv(file)
    df['Scheme'] = 'All Central Scheme'
    df_list.append(df)
    print(file)
    
# Read All IAY New Construction Data
iay_folder = os.path.join(data_folder, "Financial Progress Reports", "IAY New Construction -done", "output")
iay_files = os.listdir(iay_folder)
iay_files = [os.path.join(iay_folder, x)  for x in iay_files if x.split('.')[-1] == 'csv'][:-1]
#df_list = []
for file in iay_files:
    df = pd.read_csv(file)
    df['Scheme'] = 'IAY New Construction'
    df_list.append(df)
    print(file)

# Read All PMAY New Construction Data
pmay_folder = os.path.join(data_folder, "Financial Progress Reports", "Pradhan Mantri Awaas Yojana -done")
pmay_files = os.listdir(pmay_folder)
pmay_files = [os.path.join(pmay_folder, x)  for x in pmay_files if x.split('.')[-1] == 'csv'][:-1]
#df_list = []
for file in pmay_files:
    df = pd.read_csv(file)
    df['Scheme'] = 'Pradhan Mantri Awaas Yojana'
    df_list.append(df)
    print(file)

df = pd.concat(df_list).reset_index()
df['Panchayat Name'] = df['A']
df = df[df['Panchayat Name'].notnull()]
df['Panchayat Name'] = df['Panchayat Name'].str.upper()
df['Panchayat Name'] = df['Panchayat Name'].str.replace('PANCHAYAT', '').str.replace('GP', '')
df['District Name'] = df['District Name'].str.upper()
df['State Name'] = df['State Name'].str.upper()
df['dyear'] = df['Financial Year'].str.split('-').str[0].fillna(0).astype(int)
df['district_y'] = df['District Name'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
df['panchayat_y'] = df['Panchayat Name'].str.upper().str.replace('([^A-Za-z]+)', '').apply(remove_consecutive_duplicates).str.strip()
df = pd.merge(df, geocoded_df, how='left', on=['panchayat_y', 'district_y'])
# Output to CSV
df.to_csv(os.path.join(output_folder, 'joined', "Financial Progress Reports.csv"), encoding='utf-8', index=False)
df

E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset at assembly constituency level\data\Financial Progress Reports\All Central Scheme-done\output\2010-2011_Scrapped_Data.csv
E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset at assembly constituency level\data\Financial Progress Reports\All Central Scheme-done\output\2011-2012_Scrapped_Data.csv
E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset at assembly constituency level\data\Financial Progress Reports\All Central Scheme-done\output\2012-2013_Scrapped_Data.csv
E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset at assembly constituency level\data\Financial Progress Reports\All Central Scheme-done\output\2013-2014_Scrapped_Data.csv
E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset at assembly constituency level\data\Financial Progress Reports\All Central Scheme-done\output\2014-2015_Scrapped_Data.csv
E:\workspace\sourav sarkar\Task 13 - Prepare Awas Yojana dataset 

level_0  index                              A       B       C  \
0              0      0                     Haldhia GP   0.000   0.000   
1              1      0                       Misamara   0.000   0.485   
2              2      0              Kankalash-Bashail   0.000   0.000   
3              3      1                 SOUTH BADARPUR   0.000   0.000   
4              4      0                    Gopal Nagar   0.000   0.000   
5              5      0                        BORGANG   0.000   0.000   
6              6      0                  NO.1 BIHAGURI   0.000   0.000   
7              7      0         Araria Basti Panchayat   0.000   0.000   
8              8      1              Bangama Panchayat   0.000   0.000   
9              9      2             Bansbari Panchayat   0.000   0.000   
10            10      3                Belwa Panchayat   0.000   0.000   
11            11      4                Bochi Panchayat   0.000   0.000   
12            12      5           Chandardei Panchayat   3.000   0.000   
13            13      6               Chatar Panchayat  39.299   4.500   
14            14      7               Chikni Panchayat   0.000   0.000   
15            14      7               Chikni Panchayat   0.000   0.000   
16            15      8              Gaiyari Panchayat   0.000   0.000   
17            16      9             Hayatpur Panchayat   0.300   0.000   
18            17     10                Jamua Panchayat   0.000   0.000   
19            18     11               Jhamta Panchayat   0.000   0.000   
20            19     12            Kamaldaha Panchayat   0.750   0.000   
21            19     12            Kamaldaha Panchayat   0.750   0.000   
22            20     13     Kismat Khawaspur Panchayat   0.000   0.000   
23            21     14          Kusiyargaon Panchayat   0.000   0.000   
24            22     15         Madanpur (E) Panchayat   6.600   0.000   
25            23     16         Madanpur (W) Panchayat   1.800   0.000   
26            24     17             Paiktola Panchayat   0.000   0.000   
27            25     18            Pakhariya Panchayat   0.750   0.000   
28            26     19  Rampur Mohanpur (E) Panchayat   0.000   0.000   
29            27     20             Sahasmal Panchayat   4.200   0.000   
...          ...    ...                            ...     ...     ...   
2760154   183674      5                     Bandahalli  12.732   0.373   
2760155   183675      6                      Belagundi   2.246   0.000   
2760156   183676      7                      Chandraki   0.000   0.000   
2760157   183677      8                       Chapatla  36.307   0.000   
2760158   183678      9                     Chinnakara   1.123   0.000   
2760159   183679     10                       Gajarkot   1.498   0.000   
2760160   183680     11                       Haligera  13.841   9.730   
2760161   183681     12                      Hattikuni   2.988   1.867   
2760162   183682     13                        Jaigram   5.986   0.000   
2760163   183683     14                       Kadechur   0.748   0.748   
2760164   183684     15                   Kalebelgunda   0.746   0.000   
2760165   183685     16                       Kandkuru  11.974   0.000   
2760166   183686     17                     Killankera   6.361   2.246   
2760167   183687     18                         Konkal   1.123   0.373   
2760168   183688     19                        Kouluru   2.619   3.740   
2760169   183689     20                         Madwar   0.375   0.748   
2760170   183690     21                         Malhar   2.617   1.496   
2760171   183691     22                       Minaspur   0.746   0.748   
2760172   183692     23                       Motnalli   1.498   0.000   
2760173   183693     24                         Mudnal  10.109   0.000   
2760174   183694     25                       Mundargi   5.990   3.369   
2760175   183695     26                        Paspool  35.170   1.871   
2760176   183